## Imports

In [1]:
import pandas as pd
import numpy as np
import folium
import geopandas as gpd
import os
from textwrap import shorten

## Data read-in

state lines file: https://www.census.gov/cgi-bin/geo/shapefiles/index.php?year=2022&layergroup=States+%28and+equivalent%29

In [2]:
states_gdf = gpd.read_file('tl_2022_us_state/')

In [3]:
lawsuits_df = pd.read_csv('NAR_map_template_popup_pin - Lawsuits.csv')
print(lawsuits_df.columns)

Index(['Plaintiffs', 'Defendants', 'State lawsuit was filed in', 'Stage',
       'Summary', 'link to complaint PDF', 'story_link'],
      dtype='object')


In [4]:
rules_df = pd.read_csv('NAR_map_template_popup_pin - RuleChanges.csv')
print(rules_df.columns)

Index(['Entity', 'State', 'Summary', 'story_link', 'additional_links'], dtype='object')


## Make Map

In [5]:
# Create a new column with HTML-formatted text and hyperlinks (with exception handling)
def create_description_with_link(row):
    short_description = shorten(row["Summary"], width=20, placeholder="")
    story_link = row["story_link"]
    
    if pd.notna(story_link) and story_link.strip() != "":
        return f'<a href="{story_link}" target="_blank" rel="noopener noreferrer">{short_description}</a>{row["Summary"].replace(short_description, "", 1)}'
    else:
        return row["Summary"]

lawsuits_df["Summary"] = lawsuits_df.apply(create_description_with_link, axis=1)

In [6]:
# Create summary link for complaints
lawsuits_df['lawsuit_link_holder'] = 'Complaint Link'

lawsuits_df['short_description'] = lawsuits_df['lawsuit_link_holder'].apply(lambda s: shorten(s, width=20, placeholder=""))
lawsuits_df['remaining_desc'] = lawsuits_df.apply(lambda row : row['lawsuit_link_holder'].replace(str(row['short_description']), ''), axis=1)
lawsuits_df['remaining_desc']

lawsuits_df["description_link"] = '<a href="' + lawsuits_df["link to complaint PDF"] + '" target="_blank" rel="noopener noreferrer">' + lawsuits_df["short_description"] + "</a>" + lawsuits_df["remaining_desc"]
lawsuits_df['lawsuit_link_holder'] = lawsuits_df['description_link']

lawsuits_df['lawsuit_link_holder'] = lawsuits_df['lawsuit_link_holder'].fillna('Not available')


In [7]:
rules_df["short_description"] = rules_df["Summary"].apply(lambda s: shorten(s, width=20, placeholder=""))
rules_df['remaining_desc'] = rules_df.apply(lambda row : row['Summary'].replace(str(row['short_description']), ''), axis=1)

rules_df["description_link"] = '<a href="' + rules_df["additional_links"] + '" target="_blank" rel="noopener noreferrer">' + rules_df["short_description"] + "</a>" + rules_df["remaining_desc"]
rules_df['Summary'] = rules_df['description_link']

In [8]:
# Group the lawsuit DataFrame by 'State lawsuit was filed in' and aggregate the details into a list of dictionaries
lawsuit_details = lawsuits_df.groupby('State lawsuit was filed in').apply(lambda x: x.to_dict('records')).reset_index(name='Details')

rules_details = rules_df.groupby('State').apply(lambda x: x.to_dict('records')).reset_index(name='Details')

In [9]:
# Merge the aggregated lawsuit data with the GeoDataFrame
merged_gdf = states_gdf.merge(lawsuit_details, left_on='NAME', right_on='State lawsuit was filed in')

In [10]:
merged_gdf_rules = states_gdf.merge(rules_details, left_on='NAME', right_on='State')

In [11]:
def format_lawsuit_info(lawsuits):
    # Start the HTML table
    info = '<table style="border-collapse: collapse; width: 100%;">'
    info += '''
    <tr>
        <th style="border: 1px solid black; padding: 5px;">Plaintiff</th>
        <th style="border: 1px solid black; padding: 5px;">Defendant</th>
        <th style="border: 1px solid black; padding: 5px;">Stage</th>
        <th style="border: 1px solid black; padding: 5px;">Complaint</th>
        <th style="border: 1px solid black; padding: 5px;">Summary</th>
    </tr>
    '''
    # Loop through each lawsuit and add it to the table
    for lawsuit in lawsuits:
        plaintiff = lawsuit['Plaintiffs']  # Adjusted key
        defendant = lawsuit['Defendants']  # Adjusted key
        stage = lawsuit['Stage']
        complaint = lawsuit['lawsuit_link_holder']
        summary = lawsuit['Summary']       # Adjusted key
        
        info += f'''
        <tr>
            <td style="border: 1px solid black; padding: 5px;">{plaintiff}</td>
            <td style="border: 1px solid black; padding: 5px;">{defendant}</td>
            <td style="border: 1px solid black; padding: 5px;">{stage}</td>
            <td style="border: 1px solid black; padding: 5px;">{complaint}</td>
            <td style="border: 1px solid black; padding: 5px;">{summary}</td>
        </tr>
        '''
    info += '</table>'
    return info

In [12]:
def format_rules_info(rules):
    # Start the HTML table
    info_2 = '<table style="border-collapse: collapse; width: 100%;">'
    info_2 += '''
    <tr>
        <th style="border: 1px solid black; padding: 5px;">Entity</th>
        <th style="border: 1px solid black; padding: 5px;">State</th>
        <th style="border: 1px solid black; padding: 5px;">Summary</th>
    </tr>
    '''
    # Loop through each lawsuit and add it to the table
    for rule in rules:
        entity = rule['Entity']  # Adjusted key
        state = rule['State']  # Adjusted key
        summary = rule['Summary']

        info_2 += f'''
        <tr>
            <td style="border: 1px solid black; padding: 5px;">{entity}</td>
            <td style="border: 1px solid black; padding: 5px;">{state}</td>
            <td style="border: 1px solid black; padding: 5px;">{summary}</td>
        </tr>
        '''
    info_2 += '</table>'
    return info_2

In [13]:
# Convert the merged GeoDataFrame to GeoJSON
merged_geojson = merged_gdf.to_json()

merged_geojson_rules = merged_gdf_rules.to_json()

# Initialize the map centered around the continental US
m = folium.Map(location=[37.0902, -95.7129], zoom_start=4, tiles=None)

title_html = '''
              <h3 align="center" style="font-size:16px"><b>{}</b></h3>
             '''.format(f'Lawsuits and rule changes involving commissions')

# Create the GeoJson object
geojson_obj = folium.GeoJson(
    merged_geojson,
    name='Lawsuits',
    style_function=lambda x: {'fillColor': 'blue', 'color': 'black'}
)

geojson_obj_rules = folium.GeoJson(
    merged_geojson_rules,
    name='Rule Changes',
    style_function=lambda x: {'fillColor': 'green', 'color': 'black'}
)

# Iterate over each feature in the GeoJSON data
for feature in geojson_obj.data['features']:
    state_name = feature['properties']['NAME']
    
    # Filter the merged_gdf for the current state's lawsuits
    state_lawsuits = merged_gdf[merged_gdf['NAME'] == state_name]

    # Check if there are any lawsuits for the current state
    if not state_lawsuits.empty:
        # Get the lawsuits details for the current state
        lawsuits = state_lawsuits['Details'].values.tolist()[0]  # Convert to list if not already

        # Format the HTML content for the popup
        popup_content = format_lawsuit_info(lawsuits)

        # Create a popup and attach it to the feature on the map
        popup = folium.Popup(html=popup_content, max_width=450)
        folium.Marker(
            location=[float(feature['properties']['INTPTLAT']), float(feature['properties']['INTPTLON'])],
            popup=popup,
            icon=folium.Icon(icon='gavel', prefix='fa', color='orange')  # Using Font Awesome's 'gavel' icon
        ).add_to(geojson_obj)
        
# Iterate over each feature in the GeoJSON data
for feature in geojson_obj_rules.data['features']:
    state_name = feature['properties']['NAME']
    
    # Filter the merged_gdf for the current state's lawsuits
    state_rules = merged_gdf_rules[merged_gdf_rules['NAME'] == state_name]

    # Check if there are any lawsuits for the current state
    if not state_rules.empty:
        # Get the lawsuits details for the current state
        rules = state_rules['Details'].values.tolist()[0]  # Convert to list if not already

        # Format the HTML content for the popup
        popup_content = format_rules_info(rules)

        # Create a popup and attach it to the feature on the map
        popup = folium.Popup(html=popup_content, max_width=450)
        folium.Marker(
            location=[float(feature['properties']['INTPTLAT']), float(feature['properties']['INTPTLON'])],
            popup=popup,
            icon=folium.Icon(icon='book', prefix='fa', color='red')  # Using Font Awesome's 'gavel' icon
        ).add_to(geojson_obj_rules)

# Add tooltips to the GeoJson object
tooltip = folium.GeoJsonTooltip(fields=['NAME'], aliases=['State:'])
geojson_obj.add_child(tooltip)

tooltip_2 = folium.GeoJsonTooltip(fields=['NAME'], aliases=['State:'])
geojson_obj_rules.add_child(tooltip_2)

# Add the GeoJson object to the map
geojson_obj.add_to(m)
geojson_obj_rules.add_to(m)

folium.TileLayer('OpenStreetMap',control=False).add_to(m)

folium.map.LayerControl(collapsed=False).add_to(m)

# Add title
m.get_root().html.add_child(folium.Element(title_html))

# Display the map
m

In [14]:
m.save('index.html')

In [15]:
base_name = 'https://trd-digital.github.io/trd-news-interactive-maps/'

cwd = os.getcwd()

cwd = cwd.split('/')

final_name = base_name + cwd[-1]
print(final_name)

https://trd-digital.github.io/trd-news-interactive-maps/NAR_lawsuit_map
